# A 5-min intro to Julia

## Functions and multiple dispatch 

In [ ]:
function mysquare(x)
    x * x
end

# or alternatively just:
mysquare(x) = x * x

In [ ]:
mysquare(3)    # Integer arithmetic

In [ ]:
mysquare(2im)  # Complex arithmetic

### Lists == Arrays == Vectorisation

In [ ]:
typeof(["abc"])

In [ ]:
typeof([1, 2, 3])

In [ ]:
typeof([1.1, 2, 3])

In [ ]:
typeof(["abc", 1, 2.3])

In [ ]:
arr = [1.1, 2, 3]
mysquare.(arr)   # Vectorised call

In [ ]:
sin.(exp.(mysquare.(arr)))

# or:
@. sin(exp(mysquare(arr)))

### Changing precision

In [ ]:
Type = Float16

a = rand(Type, 3, 4)
sum(mysquare.(a))

### Changing computational backend

In [ ]:
using StaticArrays

# Array operations on static-sized arrays:
a = @SArray[1,2,3,4]
mysquare.(a)

In [ ]:
using SparseArrays

# random sparse array
a = sprandn(6, 6, 0.3)
mysquare.(a)

In [ ]:
using Distributed

# Add 4 processes and setup environment at each of them
#addprocs(4)

@everywhere begin
    mysquare(x) = x * x
    using DistributedArrays
end

a = drandn(100,100,10)
println(sum(mysquare.(a)))
close(a)

## Automatic differentiation (Adjoint mode)

- FD and Forward well-established
- Adjoint mode: Many packages, Zygote very promising, but experimental

In [ ]:
using Zygote
using SpecialFunctions

f(x) = 2x*sin(x) - x^2/2 

In [ ]:
@time f'(1)

In [ ]:
@time f'(2)

In [ ]:
@time f''(2)

## Two-way integration with existing codes
- e.g. `python`, `C++`, `Fortan`, `R`

In [ ]:
# Call to lapack to compute dot product
v = [1.0, 2.0, 3.0, 4.0]
w = [2.0, 3.0, 4.0, 5.0]

VdotW = ccall((:ddot_, "liblapack"), Float64,
              (Ref{Int32}, Ptr{Float64}, Ref{Int32}, Ptr{Float64}, Ref{Int32}),
              length(v), v, 1, w, 1)
println("v ⋅ w = $VdotW")

In [ ]:
# Plot function in matplotlib
using PyPlot

# f defined as above
x = collect(-4:0.2:7)
PyPlot.plot(x, f.(x), label="f(x) = 2x*sin(x) - x^2/2 ")
PyPlot.plot(x, f'.(x), label="f'(x)")
PyPlot.plot(x, f''.(x), label="f''(x)")
PyPlot.axhline(0, color="grey", linewidth=0.5)
PyPlot.legend()
PyPlot.show()